In [1]:
import numpy as np
import pandas as pd
import time

In [2]:
music_df = pd.read_csv('Q Learning data_0615.csv')

In [3]:
music_df

music_cluster  times
0               2     10
1               1      1
2               4     22
3               3     13
4               4     25
5               3     17
6               5     28
7               1      2
8               5     30
9               5     29
10              2      7
11              2      8
12              3     15
13              1      0
14              4     24
15              4     26
16              2      9
17              3     19
18              5     30
19              1      0

In [4]:
N_STATES = 20   # 1维世界的寬度
ACTIONS = ['very dislike', 'dislike', 'soso', 'like', 'very like']     # 探索者的可用動作
EPSILON = 0.9   # 貪婪度 greedy
ALPHA = 0.1     # 學習率
GAMMA = 0.9    # 獎勵遞減值
MAX_EPISODES = 13   # 最大回合數
FRESH_TIME = 0.3    # 移動間隔時間

In [5]:
def build_q_table(n_states, actions):
    table = pd.DataFrame(
        np.zeros((n_states, len(actions))),     # q_table初始全0
        columns = actions,    # columns對應的是行為名稱
    )
    return table

In [6]:
build_q_table(N_STATES, ACTIONS)

very dislike  dislike  soso  like  very like
0            0.0      0.0   0.0   0.0        0.0
1            0.0      0.0   0.0   0.0        0.0
2            0.0      0.0   0.0   0.0        0.0
3            0.0      0.0   0.0   0.0        0.0
4            0.0      0.0   0.0   0.0        0.0
5            0.0      0.0   0.0   0.0        0.0
6            0.0      0.0   0.0   0.0        0.0
7            0.0      0.0   0.0   0.0        0.0
8            0.0      0.0   0.0   0.0        0.0
9            0.0      0.0   0.0   0.0        0.0
10           0.0      0.0   0.0   0.0        0.0
11           0.0      0.0   0.0   0.0        0.0
12           0.0      0.0   0.0   0.0        0.0
13           0.0      0.0   0.0   0.0        0.0
14           0.0      0.0   0.0   0.0        0.0
15           0.0      0.0   0.0   0.0        0.0
16           0.0      0.0   0.0   0.0        0.0
17           0.0      0.0   0.0   0.0        0.0
18           0.0      0.0   0.0   0.0        0.0
19           0.0      0.0   0.0   0.0        0.0

In [7]:
realA_List = []
for i in range (len(music_df)):
    times = music_df["times"][i]
    if 0 <= times <= 3:
        realA = 'very dislike'
        realA_List.append(realA)
    elif 4 <= times <= 10:
        realA = 'dislike'
        realA_List.append(realA)
    elif 11 <= times <= 19:
        realA = 'soso'
        realA_List.append(realA)
    elif 20 <= times <= 27:
        realA = 'like'
        realA_List.append(realA)
    elif 28 <= times <= 30:
        realA = 'very like'
        realA_List.append(realA)
print(realA_List)

['dislike', 'very dislike', 'like', 'soso', 'like', 'soso', 'very like', 'very dislike', 'very like', 'very like', 'dislike', 'dislike', 'soso', 'very dislike', 'like', 'like', 'dislike', 'soso', 'very like', 'very dislike']


In [8]:
# 在某個state地點，選擇行為
def choose_action(state, q_table):
    state_actions = q_table.iloc[state, :]  # 選出這個state的所有action值
    #print('state_actions:','\n',state_actions)
    if (np.random.uniform() > EPSILON) or (state_actions.all() == 0):  # 非貪婪 or 或者這個 state 還沒有探索過
        action_name = np.random.choice(ACTIONS)
    else:
        action_name = state_actions.argmax()    # 貪婪模式
    return action_name

In [15]:
def action(times):
    realA_L = []
    if 0 <= times <= 3:
        realA = 'very dislike'
        realA_L.append(realA)
    elif 4 <= times <= 10:
        realA = 'dislike'
        realA_L.append(realA)
    elif 11 <= times <= 19:
        realA = 'soso'
        realA_L.append(realA)
    elif 20 <= times <= 27:
        realA = 'like'
        realA_L.append(realA)
    elif 28 <= times <= 30:
        realA = 'very like'
        realA_L.append(realA)
    return realA_L

In [16]:
def get_env_feedback(S,A,realA):

    if A == realA:
        R = 1
        if S == N_STATES - 1:
            S_ = 'terminal'
        else:
            S_ = S + 1
    
    else:       
        if realA == 'very dislike':
            R = 0
            if S == 0:
                S_ = S
            else:
                S_ = S - 1

        elif realA == 'dislike':
            R = 0
            if S == 0:
                S_ = S 
            else:
                S_ = S - 1

        elif realA == 'soso':
            R = 0
            if S == 0:
                S_ = S
            else:
                S_ = S

        elif realA == 'like':
            R = 0
            if S == 0:
                S_ = S
            else:
                S_ = S + 1
        
        elif realA == 'very like':
            R = 0
            if S == 0:
                S_ = S 
            else:
                S_ = S + 1

    return S_, R

In [29]:
def rl():
    q_table = build_q_table(N_STATES, ACTIONS)  # 初始 q table
    
    for i in range(len(music_df)):     # 回合數
        
        S = music_df["music_cluster"][0] - 1   # 回合初始位置

        is_terminated = False   # 是否回合結束   
            
        while not is_terminated:  # not後面為False，執行冒號後面指令
            
            count = 0
            
            #for i in range (len(music_df)):
                #times =  music_df['times'][i]
                #action(times)
            
            A = choose_action(S, q_table)   # 選隨機行為
            realA_L = action(times)
            realA = realA_L[count]
            #print(A)
            #print(realA)
            print('i：',i,'|','隨機行為：',A,'|','真實行為：',realA)

23
            print("R: ",R)
            print()

            q_predict = q_table.loc[S, A]    # 估算的(狀態-行為)值

            if S_ != 'terminal':
                q_target = R + GAMMA * q_table.iloc[S_, :].max()   # 實際的(狀態-行為)值 (回合沒結束)
            else:
                q_target = R     # 實際的(狀態-行為)值 (回合結束)
                is_terminated = True    # terminate this episode

            q_table.loc[S, A] += ALPHA * (q_target - q_predict)  # q_table更新
            S = S_  # 移動到下一個 state
        
            count += 1
            
        print('is_terminated:',is_terminated)

    return q_table

In [30]:
if __name__ == "__main__":
    q_table = rl()
    print('===== DONE =====')

i： 0 | 隨機行為： soso | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  1
R:  1

i： 0 | 隨機行為： soso | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  1
R:  1

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  2
R:  1

i： 0 | 隨機行為： like | 真實行為： very dislike
S_:  1
R:  0

i： 0 | 隨機行為： soso | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： like | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： like | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： like | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： very like | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： soso | 真實行為： very dislike
S_:  0
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  1
R

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: FutureWarning: 'argmax' is deprecated, use 'idxmax' instead. The behavior of 'argmax'
will be corrected to return the positional maximum in the future.
Use 'series.values.argmax' to get the position of the maximum now.
  



i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  4
R:  1

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  6
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  5
R:  0

i： 0 | 隨機行為： very like | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： soso | 真實行為： very dislike
S_:  3
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  4
R:  1

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  6
R:  1

i： 0 | 隨機行為： very like | 真實行為： very dislike
S_:  5
R:  0

i： 0 | 隨機行為： like | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  3
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  4
R:  1

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： like | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 

R:  1

i： 0 | 隨機行為： very like | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： very like | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  0

i： 0 | 隨機行為： very dislike | 真實行為： very dislike
S_:  5
R:  1

i： 0 | 隨機行為： dislike | 真實行為： very dislike
S_:  4
R:  

...

R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 10 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 10 | 隨機行為： very dislike | 真實行為： very dislike
S

i： 12 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 12 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 12 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 12 | 隨機行為： dislike | 真實行為： very dislike
S_:  17
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  18
R:  1

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 12 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 12 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 12 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 12 | 隨機行為： dislike | 真實行為： very dislike
S_:  17
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  18
R:  1

i： 12 | 隨機行為： dislike | 真實行為： very dislike
S_:  17
R:  0

i： 12 | 隨機行為： very dislike | 真實行為： very dislike
S_:  18

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  6
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  7
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  8
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  9
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  10
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  11
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  12
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  13
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  14
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  15
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  16
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  17
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  18
R:  1

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 14 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 14 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 1

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 18 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 18 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19


i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  17
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  18
R:  1

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i： 19 | 隨機行為： very dislike | 真實行為： very dislike
S_:  19
R:  1

i： 19 | 隨機行為： like | 真實行為： very dislike
S_:  18
R:  0

i

In [31]:
print('\r\nQ-table:')
q_table


Q-table:


very dislike   dislike      soso      like  very like
0       1.122332  0.070325  0.017173  0.046539   0.017173
1       5.937836  0.129248  0.098693  0.117919   0.054653
2       6.785755  0.031400  0.044073  0.067495   0.065667
3       6.872998  1.169435  1.486060  0.680062   2.365888
4       6.869217  5.374952  5.238903  5.262742   5.407834
5       6.839654  5.227355  5.373671  5.280250   5.333841
6       6.855586  5.359126  5.240029  5.248210   5.291087
7       6.842848  5.287037  5.264117  5.177695   5.386086
8       6.879210  5.222005  5.252953  5.330520   5.293336
9       6.852726  5.388684  5.187623  5.231562   5.262671
10      6.833441  5.218579  5.339854  5.279437   5.243001
11      6.798540  5.380991  5.336881  5.322120   5.399278
12      6.729819  5.251305  5.298173  5.357316   5.290006
13      6.643292  5.275711  5.232231  5.265643   5.236977
14      6.473743  5.254157  5.266715  5.293887   5.322047
15      6.252250  5.265802  5.285627  5.354878   5.257212
16      6.032329  5.269651  5.294825  5.195410   5.238588
17      5.734449  5.195242  5.180794  5.162273   5.159694
18      5.262665  5.060961  4.982082  5.025405   5.006882
19      0.878423  3.874724  3.957553  4.736339   3.408947